# ทดสอบการค้นคืนข่าวที่น่าชื่อถือจากทุกแหล่ง (cofact/anti/sure) ด้วย cosine similarity + TF-IDF (ใช้เฉพาะหัวข้อข่าว(header จาก cofact_refer + anti_info + sure_info.json) 10/12/2021)

In [1]:
import numpy as np
import nltk
import re
import pandas as pd 
import json
import os
import pickle
import csv

from pythainlp import word_tokenize
from pythainlp.corpus import thai_stopwords
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words
from string import punctuation

from sklearn.preprocessing import normalize
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from scipy import spatial

from ast import literal_eval

nltk.download('words')
th_stop = thai_stopwords()
en_stop = get_stop_words('en')
p_stemmer = PorterStemmer()

def split_word(text):
    tokens = word_tokenize(text,engine='newmm')
    
    # Remove stop words ภาษาไทย และอักขระพิเศษ
    tokens = [i for i in tokens if (not i in th_stop) & (not i in en_stop) & (not i in punctuation) & (not i in ["'",'"','“','”','‘','’','\n',"None", ' '])] 
    
    # ลบตัวเลข
    tokens = [i for i in tokens if not i.isnumeric()]
    
    # ลบช่องว่าง
    tokens = [i for i in tokens if not ' ' in i]

    return tokens

def remove_emojis(data):
    emoj = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)
    return re.sub(emoj, '', data)

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\Administrator\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


## ดึงข้อมูลของ cofact

In [82]:
def read_cofact_refer():
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../Scrapy/Scrapy_project/spiders/results/cofact/cofact_refer.csv')
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)

    # read header from CSV file
    header = []
    header = next(csvreader)
    
    rows = []
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        tmp.append(row[1])

        content_parts = literal_eval(row[2])
        content = ''.join(filter(None, content_parts))
        
        tmp.append(content)
        tmp.append(row[3])
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [83]:
cofact_refer_text_list = read_cofact_refer()

In [84]:
cofact_refer_text_list

[['น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเชื่อ',
  'มีการแชร์ให้เห็นอยู่บ่อยว่า มีน้ำชาดื่มแล้วรักษาอาการแพ้อาหารได้ ซึ่งความเป็นจริงนั้นไม่สามารถทำได้ อาการแพ้อาหาร เป็นปฏิกิริยาตอบสนองของระบบภูมิคุ้มกันในร่างกายที่เกิดขึ้นหลังจากที่ผู้ป่วยรับประทานอาหารบางชนิดเข้าไป โดยอาจทำให้เกิดอาการที่มีความผิดปกติเกี่ยวกับทางเดินอาหารทางเดินหายใจ ผิวหนัง หรือระบบหลอดเลือดและหัวใจ ในบางรายอาจทำให้เกิดโรคภูมิแพ้ชนิดรุนแรงซึ่งมีอาการที่รุนแรงและอาจเป็นอันตรายถึงแก่ชีวิตได้',
  'https://sure.oryor.com/index.php/detail/media_specify/605'],
 ['มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ',
  'เอาอีกแล้ว ไม่เช็คให้ชัวร์ แล้วก็แชร์กันไปมั่ว ๆ ว่า เอามะนาวกับเกลือมาถูหน้าผากแก้ไมเกรนได้ ความจริง การนำมะนาวหรือน้ำมะนาวหรือเกลือมาถูบริเวณหน้าผาก ไม่สามารถดูดซึมสารใดๆ ที่เป็นประโยชน์ในการบรรเทาอาการปวดไมเกรนเข้าสู่ร่างกายได้เลย นอกจากนี้ยังอาจเกิดการระคายเคืองที่ผิวหนังจากความเป็นกรดอ่อนๆของมะนาวได้',
  'https://sure.oryor.com/index.php/detail/media_specify/426'],
 ['อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้

In [85]:
len(cofact_refer_text_list)

2317

-----------------------------------------------
## ดึงข้อมูลของ anti

In [86]:
def read_anti_refer():
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../Scrapy/Scrapy_project/spiders/results/anti/anti_info.csv')
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)
    
    # read header from CSV file
    header = []
    header = next(csvreader)

    rows = []
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        tmp.append(row[1])
        
        content_parts = literal_eval(row[2])
        content = ''.join(filter(None, content_parts))
        tmp.append(content)
        
        tmp.append(row[3])
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [87]:
anti_refer_text_list = read_anti_refer()

In [88]:
anti_refer_text_list

[['ข่าวปลอม “บิ๊กตู่” เรียกเก็บเงินภาษี 7 % “ก้าวคนละก้าว”',
  'หลังจากที่มีการนำเสนอข่าวรัฐบาลประชุมเรียกเก็บเงินภาษี 7% จากยอดเงิน 700 ล้าน ของโครงการ “ก้าวคนละก้าว” จนถูกประชาชนด่าเละ วันนี้ (10 ธ.ค.) ได้มีข่าวที่เป็นกระแสในโลกโซเชียลและเป็นที่พูดถึงกันอย่างมาก ทั้งนี้ ได้มีเว็บไซต์หนึ่งได้นำเสนอข่าว กรณีที่ทางรัฐบาลนำโดย พลเอก ประยุทธ์ จันทร์โอชา นายกรัฐมนตรี และหัวหน้า คสช. ทั้งนี้ เพจ “อีเจี๊ยบ เลียบด่วน” ได้ออกมาโพสต์แสดงความคิดต่อกรณีนี้ ว่า ข่าวดังกล่าวเป็นข่าวปลอม จะเสพข่าวอะไรต้องมีการคิดไตร่ตรองด้วย ไม่ใช่ว่าจะเชื่อไปเสียทุกเรื่อง ที่มา : ',
  'https://www.antifakenewscenter.com/%e0%b8%82%e0%b9%88%e0%b8%b2%e0%b8%a7%e0%b8%9b%e0%b8%a5%e0%b8%ad%e0%b8%a1-%e0%b8%81%e0%b9%89%e0%b8%b2%e0%b8%a7%e0%b8%84%e0%b8%99%e0%b8%a5%e0%b8%b0%e0%b8%81%e0%b9%89%e0%b8%b2%e0%b8%a7/'],
 ['เว็บคลิกเบทผุดข่าวปลอม เสี่ยตัน ไม่ช่วย พี่ตูน ชาวเน็ตด่าขรมโปรดอย่าแชร์',
  'ทำไมเรายังแชร์ข่าวปลอม! ชาวเน็ตด่าขรม เว็บคลิกเบทผุดข่าวปลอม บอก เสี่ยตัน ไม่ช่วยบริจาคเงินให้พี่ตูนในก้าวคนละก้าว ขณะที่จ่า Drama-addi

In [89]:
len(anti_refer_text_list)

2302

-----------------------------------------------
## ดึงข้อมูลของ sure

In [90]:
def read_sure_refer():
    # Opening JSON file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../Scrapy/Scrapy_project/spiders//fetch file/sure_info.json')
    f = open(path, encoding="utf8")
    
    # returns JSON object as
    # a dictionary
    sure_refer_text_data = json.load(f)

    # Closing file
    f.close()
    return sure_refer_text_data

In [91]:
sure_refer_text_data = read_sure_refer()

In [92]:
len(sure_refer_text_data)

2068

In [93]:
def get_sure_refer_info(sure_refer_text_data): #สำหรับดึงหัวข้อข่าวอ้างอิง (header) และลิงของข่าวอ้างอิง (link)
    refer_text_list = []

    for refer_text in range(len(sure_refer_text_data)):
        tmp = []
        tmp.append(sure_refer_text_data[refer_text]['header'])
        tmp.append(''.join(filter(None, sure_refer_text_data[refer_text]['content'])))
        tmp.append(sure_refer_text_data[refer_text]['link'])
        refer_text_list.append(tmp)

    return refer_text_list

In [94]:
sure_refer_text_list = get_sure_refer_info(sure_refer_text_data)

In [95]:
sure_refer_text_list

[['ชัวร์ก่อนแชร์: ตาลีบันห้ามฉีดวัคซีนโควิด 19 ในอัฟกานิสถาน จริงหรือ?',
  '17 พฤศจิกายน 2564ตรวจสอบข้อเท็จจริงโดย: Factcheck.org (สหรัฐอเมริกา)แปลและเรียบเรียงบทความโดย: พีรพล อนุตรโสตถิ์, อดิศร สุขสมอรรถประเภทข่าวปลอม: ข้อมูลเท็จบทสรุป:การฉีดวัคซีนโควิด 19 ลดลงถึง 80% นับตั้งแต่ตาลีบันยึดครองอัฟกานิสถาน แต่ UNICEF ยืนยันว่าการฉีดวัคซีนโควิด 19 ในอัฟกานิสถานยังดำเนินต่อไปWHO ประเมินว่าตัวเลขติดเชื้อและเสียชีวิตจากโควิด 19 ในอัฟกานิสถานต่ำกว่าความเป็นจริง และการแพร่ระบาดกำลังเพิ่มขึ้น3.ข้อมูลที่ถูกแชร์:มีข้อมูลเท็จเผยแพร่ทางสื่อสังคมออนไลน์ในสหรัฐอเมริกา โดยอ้างว่ากองกำลังติดอาวุธกลุ่มตาลีบัน ที่ยึดครองประเทศอัฟกานิสถานตั้งแต่เดือนสิงหาคม ออกคำสั่งห้ามฉีดวัคซีนโควิด 19 แก่ประชาชนในประเทศ สื่อให้เห็นว่าวัคซีนไม่เป็นที่ต้องการ เพราะแม้อัตราการฉีดวัคซีนในประเทศจะต่ำมาก แต่ยอดการเสียชีวิตจากโควิด 19 ในอัฟกานิสถานถือว่าน้อยกว่าหลายประเทศที่ฉีดวัคซีนกันอย่างแพร่หลายFACT CHECK: ตรวจสอบข้อเท็จจริง:นับตั้งแต่ตาลีบันยึดครองอัฟกานิสถานในช่วงเดือนสิงหาคม 2021 องค์การทุนเพื่อเด็กแห่งสหประชาชาติ (UN

In [96]:
len(sure_refer_text_list)

2068

## รวมทุก list จากทุกแหล่งข่าวเข้าด้วยกัน

In [97]:
cofact_refer_text_list[:2]

[['น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเชื่อ',
  'มีการแชร์ให้เห็นอยู่บ่อยว่า มีน้ำชาดื่มแล้วรักษาอาการแพ้อาหารได้ ซึ่งความเป็นจริงนั้นไม่สามารถทำได้ อาการแพ้อาหาร เป็นปฏิกิริยาตอบสนองของระบบภูมิคุ้มกันในร่างกายที่เกิดขึ้นหลังจากที่ผู้ป่วยรับประทานอาหารบางชนิดเข้าไป โดยอาจทำให้เกิดอาการที่มีความผิดปกติเกี่ยวกับทางเดินอาหารทางเดินหายใจ ผิวหนัง หรือระบบหลอดเลือดและหัวใจ ในบางรายอาจทำให้เกิดโรคภูมิแพ้ชนิดรุนแรงซึ่งมีอาการที่รุนแรงและอาจเป็นอันตรายถึงแก่ชีวิตได้',
  'https://sure.oryor.com/index.php/detail/media_specify/605'],
 ['มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ',
  'เอาอีกแล้ว ไม่เช็คให้ชัวร์ แล้วก็แชร์กันไปมั่ว ๆ ว่า เอามะนาวกับเกลือมาถูหน้าผากแก้ไมเกรนได้ ความจริง การนำมะนาวหรือน้ำมะนาวหรือเกลือมาถูบริเวณหน้าผาก ไม่สามารถดูดซึมสารใดๆ ที่เป็นประโยชน์ในการบรรเทาอาการปวดไมเกรนเข้าสู่ร่างกายได้เลย นอกจากนี้ยังอาจเกิดการระคายเคืองที่ผิวหนังจากความเป็นกรดอ่อนๆของมะนาวได้',
  'https://sure.oryor.com/index.php/detail/media_specify/426']]

In [98]:
anti_refer_text_list[:2]

[['ข่าวปลอม “บิ๊กตู่” เรียกเก็บเงินภาษี 7 % “ก้าวคนละก้าว”',
  'หลังจากที่มีการนำเสนอข่าวรัฐบาลประชุมเรียกเก็บเงินภาษี 7% จากยอดเงิน 700 ล้าน ของโครงการ “ก้าวคนละก้าว” จนถูกประชาชนด่าเละ วันนี้ (10 ธ.ค.) ได้มีข่าวที่เป็นกระแสในโลกโซเชียลและเป็นที่พูดถึงกันอย่างมาก ทั้งนี้ ได้มีเว็บไซต์หนึ่งได้นำเสนอข่าว กรณีที่ทางรัฐบาลนำโดย พลเอก ประยุทธ์ จันทร์โอชา นายกรัฐมนตรี และหัวหน้า คสช. ทั้งนี้ เพจ “อีเจี๊ยบ เลียบด่วน” ได้ออกมาโพสต์แสดงความคิดต่อกรณีนี้ ว่า ข่าวดังกล่าวเป็นข่าวปลอม จะเสพข่าวอะไรต้องมีการคิดไตร่ตรองด้วย ไม่ใช่ว่าจะเชื่อไปเสียทุกเรื่อง ที่มา : ',
  'https://www.antifakenewscenter.com/%e0%b8%82%e0%b9%88%e0%b8%b2%e0%b8%a7%e0%b8%9b%e0%b8%a5%e0%b8%ad%e0%b8%a1-%e0%b8%81%e0%b9%89%e0%b8%b2%e0%b8%a7%e0%b8%84%e0%b8%99%e0%b8%a5%e0%b8%b0%e0%b8%81%e0%b9%89%e0%b8%b2%e0%b8%a7/'],
 ['เว็บคลิกเบทผุดข่าวปลอม เสี่ยตัน ไม่ช่วย พี่ตูน ชาวเน็ตด่าขรมโปรดอย่าแชร์',
  'ทำไมเรายังแชร์ข่าวปลอม! ชาวเน็ตด่าขรม เว็บคลิกเบทผุดข่าวปลอม บอก เสี่ยตัน ไม่ช่วยบริจาคเงินให้พี่ตูนในก้าวคนละก้าว ขณะที่จ่า Drama-addi

In [99]:
sure_refer_text_list[:2]

[['ชัวร์ก่อนแชร์: ตาลีบันห้ามฉีดวัคซีนโควิด 19 ในอัฟกานิสถาน จริงหรือ?',
  '17 พฤศจิกายน 2564ตรวจสอบข้อเท็จจริงโดย: Factcheck.org (สหรัฐอเมริกา)แปลและเรียบเรียงบทความโดย: พีรพล อนุตรโสตถิ์, อดิศร สุขสมอรรถประเภทข่าวปลอม: ข้อมูลเท็จบทสรุป:การฉีดวัคซีนโควิด 19 ลดลงถึง 80% นับตั้งแต่ตาลีบันยึดครองอัฟกานิสถาน แต่ UNICEF ยืนยันว่าการฉีดวัคซีนโควิด 19 ในอัฟกานิสถานยังดำเนินต่อไปWHO ประเมินว่าตัวเลขติดเชื้อและเสียชีวิตจากโควิด 19 ในอัฟกานิสถานต่ำกว่าความเป็นจริง และการแพร่ระบาดกำลังเพิ่มขึ้น3.ข้อมูลที่ถูกแชร์:มีข้อมูลเท็จเผยแพร่ทางสื่อสังคมออนไลน์ในสหรัฐอเมริกา โดยอ้างว่ากองกำลังติดอาวุธกลุ่มตาลีบัน ที่ยึดครองประเทศอัฟกานิสถานตั้งแต่เดือนสิงหาคม ออกคำสั่งห้ามฉีดวัคซีนโควิด 19 แก่ประชาชนในประเทศ สื่อให้เห็นว่าวัคซีนไม่เป็นที่ต้องการ เพราะแม้อัตราการฉีดวัคซีนในประเทศจะต่ำมาก แต่ยอดการเสียชีวิตจากโควิด 19 ในอัฟกานิสถานถือว่าน้อยกว่าหลายประเทศที่ฉีดวัคซีนกันอย่างแพร่หลายFACT CHECK: ตรวจสอบข้อเท็จจริง:นับตั้งแต่ตาลีบันยึดครองอัฟกานิสถานในช่วงเดือนสิงหาคม 2021 องค์การทุนเพื่อเด็กแห่งสหประชาชาติ (UN

In [100]:
all_refer_text_list = []
all_refer_text_list = cofact_refer_text_list + anti_refer_text_list + sure_refer_text_list

In [101]:
all_refer_text_list

[['น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเชื่อ',
  'มีการแชร์ให้เห็นอยู่บ่อยว่า มีน้ำชาดื่มแล้วรักษาอาการแพ้อาหารได้ ซึ่งความเป็นจริงนั้นไม่สามารถทำได้ อาการแพ้อาหาร เป็นปฏิกิริยาตอบสนองของระบบภูมิคุ้มกันในร่างกายที่เกิดขึ้นหลังจากที่ผู้ป่วยรับประทานอาหารบางชนิดเข้าไป โดยอาจทำให้เกิดอาการที่มีความผิดปกติเกี่ยวกับทางเดินอาหารทางเดินหายใจ ผิวหนัง หรือระบบหลอดเลือดและหัวใจ ในบางรายอาจทำให้เกิดโรคภูมิแพ้ชนิดรุนแรงซึ่งมีอาการที่รุนแรงและอาจเป็นอันตรายถึงแก่ชีวิตได้',
  'https://sure.oryor.com/index.php/detail/media_specify/605'],
 ['มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ',
  'เอาอีกแล้ว ไม่เช็คให้ชัวร์ แล้วก็แชร์กันไปมั่ว ๆ ว่า เอามะนาวกับเกลือมาถูหน้าผากแก้ไมเกรนได้ ความจริง การนำมะนาวหรือน้ำมะนาวหรือเกลือมาถูบริเวณหน้าผาก ไม่สามารถดูดซึมสารใดๆ ที่เป็นประโยชน์ในการบรรเทาอาการปวดไมเกรนเข้าสู่ร่างกายได้เลย นอกจากนี้ยังอาจเกิดการระคายเคืองที่ผิวหนังจากความเป็นกรดอ่อนๆของมะนาวได้',
  'https://sure.oryor.com/index.php/detail/media_specify/426'],
 ['อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้

In [102]:
len(all_refer_text_list)

6687

## ------------------------------------------------------------------------------
## สร้าง dataframe ของ cofact สำหรับอ้างถึงตอนแนบลิงค์ url แสดงผล

In [103]:
all_refer_header = []
all_refer_content = []
all_refer_url = []
for i in range(len(all_refer_text_list)):
    all_refer_header.append(all_refer_text_list[i][0]) #list ของส่วนหัวข้อข่าว
    all_refer_content.append(all_refer_text_list[i][1]) #list ของส่วนเนื้อหาเท่านั้น
    all_refer_url.append(all_refer_text_list[i][2]) #list ของ url เท่านั้น


In [104]:
#ทำ list ให้เป็น dataframe
all_original_text_and_headline_news_df = pd.DataFrame(list(zip(all_refer_header, all_refer_content, all_refer_url)), columns=["หัวข้อข่าวอ้างอิงของ ทุกแหล่งข่าว", "เนื้อหาข่าวอ้างอิงของ ทุกแหล่งข่าว", "URL ของ ทุกแหล่งข่าว"])

all_original_text_and_headline_news_df

หัวข้อข่าวอ้างอิงของ ทุกแหล่งข่าว  \
0     น้ำชาไม่สามารถรักษาโรคแพ้อาหารได้ โปรดอย่าหลงเ...   
1               มะนาวเกลือแก้ไมเกรน มั่วมาก อย่าไปเชื่อ   
2     อย่าหลงเชื่อ “นาโน สเปรย์” อ้างฆ่าเชื้อไวรัสแล...   
3         ดื่มกาแฟวันละสามแก้วทำให้หน้าอกเล็กลงไม่จริง    
4            คิ้วดกดำด้วยการทาปิโตรเลียม เจลลี่ ไม่จริง   
...                                                 ...   
6682  ชัวร์ก่อนแชร์ : ระวัง 10 ขนมขบเคี้ยวอันตราย! จ...   
6683  ชัวร์ก่อนแชร์ : เปิดแอร์ใส่หน้าเด็ก ทำให้เป็นอ...   
6684       ชัวร์ก่อนแชร์ : มะเร็งต้องเลิกบำรุงจริงหรือ?   
6685  ชัวร์ก่อนแชร์ : ยาแอสไพรินช่วยซักผ้าขาวสะอาด จ...   
6686  ชัวร์ก่อนแชร์ : เทคนิคซักผ้าด้วยเครื่องไม่ทำให...   

                     เนื้อหาข่าวอ้างอิงของ ทุกแหล่งข่าว  \
0     มีการแชร์ให้เห็นอยู่บ่อยว่า มีน้ำชาดื่มแล้วรัก...   
1     เอาอีกแล้ว ไม่เช็คให้ชัวร์ แล้วก็แชร์กันไปมั่ว...   
2     อย. เตือน!! อย่าหลงเชื่อผลิตภัณฑ์ NANO SILVER ...   
3     กาแฟเป็นเครื่องดื่มที่นิยมอย่างแพร่หลายทั่วโลก...   
4     แชร์ทั่วอินเทอร์เน็ตว่า มีคนนำปิโตรเลียม เจลลี...   
...                                                 ...   
6682  สำนักข่าวไทย 13 ก.พ.-บนโลกออนไลน์ มีการแชร์กัน...   
6683   กทม. 6 ก.พ. – โลกออนไลน์เตือนให้ระวังการให้ลู...   
6684   กทม. 30 ม.ค. – สังคมออนไลน์แชร์กันว่าให้คนเป็...   
6685  กทม. 12 เม.ย.-บนสังคมออนไลน์แชร์แนะนำเคล็ดลับซ...   
6686  กทม. 14 เม.ย.-บนสังคมออนไลน์แชร์คลิปเทคนิคการซ...   

                                   URL ของ ทุกแหล่งข่าว  
0     https://sure.oryor.com/index.php/detail/media_...  
1     https://sure.oryor.com/index.php/detail/media_...  
2     https://oryor.com/%E0%B8%AD%E0%B8%A2/detail/me...  
3     https://sure.oryor.com/index.php/detail/media_...  
4     https://sure.oryor.com/index.php/detail/media_...  
...                                                 ...  
6682                     https://tna.mcot.net/tna-93789  
6683                     https://tna.mcot.net/tna-93790  
6684                     https://tna.mcot.net/tna-93791  
6685                    https://tna.mcot.net/tna-100770  
6686                    https://tna.mcot.net/tna-101176  

[6687 rows x 3 columns]

In [105]:
all_headline_tokens_list = [split_word(txt) for txt in all_refer_header] #นำ list ของหังข้อข่าวมาตัดคำ

In [106]:
all_tokens_list_j = [','.join(tkn) for tkn in all_headline_tokens_list]

----------------------------------------------------------------------------------
# สร้าง vocabulary set

In [35]:
print(all_tokens_list_j[0].split(",")[0:2])


['น้ำชา', 'รักษาโรค']


In [36]:
## Create Vocabulary
tokens_list = []

for words in all_tokens_list_j:
    # print(words)
    temp_list = words.split(",")
    # print(temp_list)
    for i in temp_list:
        tokens_list.append(i)

vocabulary = set(tokens_list)
vocabulary = list(vocabulary)

In [37]:
len(vocabulary)

7062

--------------------------------------------------------------------------------------

In [38]:
tvec = TfidfVectorizer(analyzer=lambda x:x.split(','),)
original_c_feat = tvec.fit_transform(all_tokens_list_j)

### Save Trained TFID Model

In [39]:
### Save model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
with open(path,'wb') as handle:
    pickle.dump(original_c_feat, handle)

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


In [40]:
### load model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
t = pickle.load(open(path,'rb'))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


### Save Vocabulary

In [41]:
### Save Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "w", encoding="utf-8") as file:
    file.write(str(vocabulary))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [42]:
### load Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "r", encoding="utf-8") as file:
    data2 = eval(file.readline())

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [43]:
data2

['',
 'ปราบปราม',
 'ฉี่',
 'ต้นขา',
 'สวิส',
 'พ้อ',
 'พ่น',
 'แหงนหน้า',
 'รักษา',
 'สามแก้ว',
 'Optrix',
 'เอ',
 'ฝ่า',
 'ลิ่น',
 'จุดอ่อน',
 'รณัฐ"',
 'ชนะ',
 'น้ำยาล้างเล็บ',
 'ศ.',
 'จำหน่าย',
 'ดูแล',
 'งูพิษ',
 'สำเนา',
 'ทองพันชั่ง',
 'คาด',
 'จ่ายหนี้',
 'แท้ง',
 'ทำนาย',
 'เที่ยง',
 'ท.งด',
 'ขยับ',
 'Pro-Polis',
 'เจือจาง',
 'โลงศพ',
 'จี๊',
 'ทำเวลา',
 'ผักบุ้งจีน',
 'ฉุด',
 'พิมพา',
 'เซ็ง',
 'พิกัด',
 'อดเหล้า',
 'ติดคอ',
 'หน้าบาน',
 'พหล',
 'อิเล็กทรอนิกส์',
 'สูตร',
 'ซา',
 'ลอนดอน',
 'ชินราช',
 'คลอโรฟอร์ม',
 'สูดดม',
 'กฎ',
 'ระดับ',
 'กระทรวงการคลัง',
 'โรง',
 'e-Social',
 'โภชนาการ',
 'ความหลัง',
 'บัญชีดำ',
 'ฤดูร้อน',
 'โคเคน',
 'ข้อเสีย',
 'ข่าวดี',
 '0.250',
 'ฝากครรภ์',
 'พาวเวอร์',
 'มีเพศสัมพันธ์',
 'กล้อน',
 'ยื่นคำร้อง',
 'ไฟลต์',
 'เมือก',
 'ใยหิน',
 'ระบุ',
 'บีบบังคับ',
 'ใจเย็น',
 'ไผ่',
 'เทอร์โม',
 'จวก',
 'ดาราศาสตร์',
 'ใบ',
 'งัด',
 'AI',
 'ความรู้',
 'สะเทือนขวัญ',
 'ท้า',
 'รับสมัคร',
 'อาชีวะ',
 'บูม',
 'น้ำตา',
 'ติ่ง',
 'เห็นชอบ',
 'ริมแม่น้ำ

In [44]:
len(data2)

7062

## Create vector for Query/search keywords

In [45]:
## Create vector for Query/search keywords
def gen_vector_T(tokens):

    Q = np.zeros((len(vocabulary)))
    
    x = tvec.transform(tokens)
    
    x = x.A[0]
    return x

### Calculate Cosine similarity of trained Tfidf to input query


In [52]:
norm_original_c_feat = normalize(original_c_feat)
norm_original_c_feat = norm_original_c_feat.toarray()
norm_original_c_feat = norm_original_c_feat.T

In [53]:
query_vector = []
def cosine_similarity_T(k, query):
    tokens = split_word(str(query))
    q_df = pd.DataFrame(columns=['q_clean'])
    q_df.loc[0,'q_clean'] =str(tokens)

    q_df=q_df.replace(to_replace ="\[.", value = '', regex = True)
    q_df=q_df.replace(to_replace ="'", value = '', regex = True)
    q_df=q_df.replace(to_replace =" ", value = '', regex = True)
    q_df=q_df.replace(to_replace ='\]', value = '', regex = True)
    
    d_cosines = []
    
    query_vector = gen_vector_T(q_df['q_clean'])
    query_vector = query_vector.reshape((1,-1))

    d_cosines = np.dot(normalize(query_vector),norm_original_c_feat)
    
    list_d_cosines = d_cosines[0].tolist()
    
    out = np.array(list_d_cosines).argsort()[-k:][::-1]

    list_d_cosines.sort()
    a = pd.DataFrame()
    for i in out:
        a.loc[i,'index'] = str(i)
        a.loc[i,'headline'] = all_original_text_and_headline_news_df['หัวข้อข่าวอ้างอิงของ ทุกแหล่งข่าว'][i]

    list_d_cosines.sort(reverse=True)
    
    for j in range(k):
        a.loc[out[j],'Score'] = list_d_cosines[j]
        
    return a

In [54]:
%time all_result = cosine_similarity_T(10,'กาแฟ')

Wall time: 50 ms


In [55]:
all_result

index                                           headline     Score
805    805                      กาแฟ ต้านโควิดได้ จริงหรือไม่  0.736566
6491  6491       ชัวร์ก่อนแชร์ : 20 ประโยชน์ของกาแฟ จริงหรือ?  0.691494
6179  6179  ชัวร์ก่อนแชร์ : ดื่มกาแฟอย่างไรไม่ให้เสียให้สุ...  0.630046
5615  5615        ชัวร์ก่อนแชร์ : 5 โรคห้ามดื่มกาแฟ จริงหรือ?  0.612935
24      24                              แชร์ผิดผิด กาแฟใส่เนย  0.545241
945    945                      ดื่มชาปลอดภัยกว่ากาแฟจริงหรือ  0.532678
1461  1461                             กาแฟกับภาวะกระดูกพรุน   0.511173
6557  6557    ชัวร์ก่อนแชร์ : ชามีกาเฟอีนมากกว่ากาแฟจริงหรือ?  0.500034
5901  5901  ชัวร์ก่อนแชร์ : คลิปเตือนกาแฟผสมดินประสิว จริง...  0.458314
2891  2891  ข่าวปลอม อย่าแชร์! กาแฟสารสกัดจากธรรมชาติ ต้าน...  0.444004

In [57]:
all_result_with_url = pd.DataFrame()
for i in range(len(all_result)):
    if float(all_result.iloc[i]["Score"]) != 0.0:
        all_result_with_url.loc[i,'index'] = all_result.iloc[i]["index"]
        all_result_with_url.loc[i,'headline'] = all_result.iloc[i]["headline"]
        all_result_with_url.loc[i,'url'] = all_original_text_and_headline_news_df["URL ของ ทุกแหล่งข่าว"][int(all_result.iloc[i]["index"])]
        all_result_with_url.loc[i,'content'] = all_original_text_and_headline_news_df["เนื้อหาข่าวอ้างอิงของ ทุกแหล่งข่าว"][int(all_result.iloc[i]["index"])]

In [58]:
all_result_with_url

index                                           headline  \
0   805                      กาแฟ ต้านโควิดได้ จริงหรือไม่   
1  6491       ชัวร์ก่อนแชร์ : 20 ประโยชน์ของกาแฟ จริงหรือ?   
2  6179  ชัวร์ก่อนแชร์ : ดื่มกาแฟอย่างไรไม่ให้เสียให้สุ...   
3  5615        ชัวร์ก่อนแชร์ : 5 โรคห้ามดื่มกาแฟ จริงหรือ?   
4    24                              แชร์ผิดผิด กาแฟใส่เนย   
5   945                      ดื่มชาปลอดภัยกว่ากาแฟจริงหรือ   
6  1461                             กาแฟกับภาวะกระดูกพรุน    
7  6557    ชัวร์ก่อนแชร์ : ชามีกาเฟอีนมากกว่ากาแฟจริงหรือ?   
8  5901  ชัวร์ก่อนแชร์ : คลิปเตือนกาแฟผสมดินประสิว จริง...   
9  2891  ข่าวปลอม อย่าแชร์! กาแฟสารสกัดจากธรรมชาติ ต้าน...   

                                                 url  \
0  https://sure.oryor.com/index.php/detail/media_...   
1                     https://tna.mcot.net/tna-75433   
2                    https://tna.mcot.net/tna-197777   
3                    https://tna.mcot.net/tna-370528   
4  https://oryor.com/%E0%B8%AD%E0%B8%A2/detail/me...   
5  https://sure.oryor.com/index.php/detail/media_...   
6  https://oryor.com/%E0%B8%AD%E0%B8%A2/detail/me...   
7                      https://tna.mcot.net/tna-9776   
8                    https://tna.mcot.net/tna-278578   
9  https://www.antifakenewscenter.com/%e0%b8%82%e...   

                                             content  
0  ตอนนี้ใคร ๆ ก็กลัวการติดโรคโควิด–19 จึงมีผู้ปร...  
1  [กรุงเทพฯ 26 ก.พ. – , บนสังคมออนไลน์ มีการแชร์...  
2  [กทม. 7 เม.ย.-บนสังคมออนไลน์แชร์ 8 ข้อแนะนำดื่...  
3  [กรุงเทพฯ 11 ธ.ค. – สังคมออนไลน์แชร์เตือนผู้ป่...  
4  [ข่าวแชร์ในสื่อโซเชียลมีเดียอย่างแพร่หลายว่า ก...  
5  [สิ่งแรกในตอนเช้าที่หลาย ๆ คนมักจะทำเหมือนกันค...  
6  [กระดูกพรุน คือภาวะที่เนื้อกระดูกบางลงจากปกติ ...  
7  [สำนักข่าวไทย 9 พ.ย.-บนสังคมออนไลน์มีการแชร์ว่...  
8  [อสมท 27 ม.ค.- บนโซเชียลแชร์คลิปการทดลองฉีกซอง...  
9  [ตามที่มีข่าวปรากฏในสื่อต่างๆ เกี่ยวกับประเด็น...

---------------------------------------